In [1]:
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import matplotlib.animation as animation
from IPython.display import HTML

# Example DNA coding strand
DNA_seq = "ATGGCCATTGTAATGGGCCGCTGAAAGGGTGCCCGATAG"

# Transcription: DNA -> mRNA (T replaced by U)
mRNA_seq = DNA_seq.replace('T', 'U')
codons = [mRNA_seq[i:i+3] for i in range(0, len(mRNA_seq), 3)]

# Minimal codon table
codon_table = {
    "AUG": "M (Start)", "GCC": "A", "AUU": "I", "GUA": "V", "UGG": "W",
    "GCU": "A", "GAA": "E", "AGG": "R", "GUG": "V",
    "CCC": "P", "GAU": "D", "UAA": "Stop", "UAG": "Stop", "UGA": "Stop"
}
amino_acids = [codon_table.get(codon, "-") for codon in codons]

# Bigger figure
fig, ax = plt.subplots(figsize=(14,8))
plt.close(fig)
ax.axis('off')

def animate(frame):
    ax.clear()
    ax.axis('off')

    # Fix axis limits (so nothing gets cut off)
    ax.set_xlim(0, 1)
    ax.set_ylim(0, 1)

    # Title
    ax.set_title("Central Dogma of Molecular Biology", fontsize=18, fontweight='bold', pad=25)

    # --- DNA strand ---
    ax.text(0.05, 0.95, "DNA (Coding Strand → 5' to 3')", fontsize=14, color='#223388', fontweight='bold')
    ax.text(0.05, 0.90, " ".join(DNA_seq), fontsize=12, color='#223388', fontfamily='monospace')
    ax.plot([0.05, 0.95], [0.88, 0.88], color='#4477AA', lw=6, alpha=0.2)

    # --- Transcription stage ---
    if frame < len(mRNA_seq):
        ax.text(0.05, 0.78, "Transcription: RNA polymerase synthesizes mRNA (5'→3')",
                fontsize=13, color='purple', fontweight='bold')
        mRNA_partial = mRNA_seq[:frame+1]
        ax.text(0.05, 0.73, "mRNA (primary transcript): " + mRNA_partial,
                fontsize=12, color='purple', fontfamily='monospace')

        # RNA Polymerase
        ax.add_patch(patches.FancyBboxPatch((0.05+frame*0.014, 0.70), 0.05, 0.05,
                                            boxstyle="round,pad=0.12", linewidth=1.2,
                                            edgecolor='purple', facecolor='violet', alpha=0.9))
        ax.text(0.05+frame*0.014+0.025, 0.725, "RNA\nPolymerase", fontsize=7, color='white', ha='center')

    # --- Translation stage ---
    else:
        ax.text(0.05, 0.78, "Translation: Ribosome reads codons and builds protein",
                fontsize=13, color='green', fontweight='bold')
        ax.text(0.05, 0.73, "mRNA (mature): " + mRNA_seq, fontsize=12, color='purple', fontfamily='monospace')

        # Ribosome movement
        codon_idx = min((frame-len(mRNA_seq))//2, len(codons)-1)
        ribo_x = 0.05 + codon_idx*0.042
        ax.add_patch(patches.Circle((ribo_x+0.04, 0.70), 0.05, color='limegreen', ec='k', lw=1.2, alpha=0.9))
        ax.text(ribo_x+0.04, 0.70, "Ribosome", fontsize=7, ha='center', va='center', color='white')

        # Highlight codon
        mRNA_display = ""
        for idx, codon in enumerate(codons):
            if idx == codon_idx:
                mRNA_display += f"[{codon}] "
            else:
                mRNA_display += codon+" "
        ax.text(0.05, 0.66, "Reading codons: " + mRNA_display.strip(),
                fontsize=11, color='darkgreen', fontfamily='monospace')

        # Protein synthesis (polypeptide)
        aa_seq = " - ".join(amino_acids[:codon_idx+1])
        ax.text(0.05, 0.55, "Growing Polypeptide: " + aa_seq, fontsize=13, color='brown', fontweight='bold')

        # Draw peptide chain (orange + bonds)
        for i in range(codon_idx+1):
            ax.add_patch(patches.Circle((0.20 + i*0.05, 0.45), 0.025, color='orange', alpha=0.8, lw=0.7, ec='k'))
            if i > 0:
                ax.plot([0.20+(i-1)*0.05+0.025, 0.20+i*0.05-0.025], [0.45,0.45], color='brown', lw=1.5)

    # Legend (for clarity)
    ax.text(0.05, 0.25, "Legend:", fontsize=12, fontweight='bold')
    ax.text(0.05, 0.22, "Blue = DNA | Purple = mRNA | Green = Ribosome | Orange = Protein", fontsize=11)

    return ax,

# Animation
frames = len(mRNA_seq) + 2*len(codons)
ani = animation.FuncAnimation(fig, animate, frames=frames, interval=600, blit=False)
HTML(ani.to_jshtml())
